To do:
1. double check logstic convergence issues
2. check alpha range in supplementary repo

In [39]:
import os
import json
import pickle
import pandas as pd
import numpy as np
from sklearn.linear_model import RidgeCV, LogisticRegressionCV
from sklearn.model_selection import StratifiedKFold
from tqdm.notebook import tqdm
from rca import make_binary_scorer, make_multiclass_scorer, process_categorical, best_logistic_solver, checker, k_fold_cross_val

## Loading Data

In [2]:
# Pulling and standardising embeddings
embeds = {}
embeds_path = '../../data/raw/embeds/'
for f_name in tqdm(os.listdir(embeds_path)):
    if f_name != 'feature_overlap.csv':  # dropping since contains many NaNs
        embed = pd.read_csv(embeds_path + f_name, index_col=0)
        embed_name = f_name.split('.')[0]
        embeds[embed_name] = (embed - embed.mean()) / embed.std()

{name: embed.shape for name, embed in embeds.items()}

  0%|          | 0/26 [00:00<?, ?it/s]

{'CBOW_GoogleNews': (79279, 300),
 'PPMI_SVD_SouthFlorida': (4959, 300),
 'SVD_sim_rel': (6002, 300),
 'spherical_text_Wikipedia': (59012, 300),
 'norms_sensorimotor': (36854, 11),
 'fastText_Wiki_News': (81728, 300),
 'PPMI_SVD_EAT': (7775, 300),
 'GloVe_Twitter': (48614, 200),
 'LexVec_CommonCrawl': (87635, 300),
 'fastTextSub_OpenSub': (72538, 300),
 'eye_tracking': (7486, 6),
 'SGSoftMaxOutput_SWOW': (25442, 300),
 'morphoNLM': (50506, 50),
 'SGSoftMaxInput_SWOW': (11783, 300),
 'fMRI_text_hyper_align': (1205, 1000),
 'GloVe_Wikipedia': (68943, 300),
 'EEG_text': (3355, 104),
 'fastText_CommonCrawl': (88986, 300),
 'fMRI_speech_hyper_align': (579, 6),
 'compo_attribs': (534, 62),
 'PPMI_SVD_SWOW': (11783, 300),
 'microarray': (626, 15),
 'EEG_speech': (1591, 130),
 'GloVe_CommonCrawl': (88440, 300),
 'THINGS': (1562, 49)}

In [18]:
norms = pd.read_csv('../../data/raw/psychNorms.zip', index_col=0, compression='zip', low_memory=False)
norm_metadata = pd.read_csv('../../data/raw/psychNorms_metadata.csv', index_col='norm')
norm_metadata['associated_embed'] = norm_metadata['associated_embed'].astype(str)
norms

Freq_HAL  Freq_KF  Freq_SUBTLEXUS  Freq_SUBTLEXUK  Freq_Blog  \
'em               0.0      NaN             NaN             NaN        NaN   
'neath            0.0      NaN             NaN             NaN        NaN   
're               0.0      NaN             NaN             NaN        NaN   
'shun             0.0      NaN             NaN             NaN        NaN   
'tis              0.0      NaN             NaN             NaN        NaN   
...               ...      ...             ...             ...        ...   
shrick            NaN      NaN             NaN             NaN        NaN   
post office       NaN      NaN             NaN             NaN        NaN   
fishing rod       NaN      NaN             NaN             NaN        NaN   
March             NaN      NaN             NaN             NaN        NaN   
May               NaN      NaN             NaN             NaN        NaN   

             Freq_Twitter  Freq_News  Freq_CobW  Freq_CobS  CD_SUBTLEXUS  ...  \
'em                   NaN        NaN     1.3617     1.9138           NaN  ...   
'neath                NaN        NaN     0.0000     0.0000           NaN  ...   
're                   NaN        NaN     0.9031     1.6335           NaN  ...   
'shun                 NaN        NaN     0.0000     0.0000           NaN  ...   
'tis                  NaN        NaN     0.4771     0.6021           NaN  ...   
...                   ...        ...        ...        ...           ...  ...   
shrick                NaN        NaN        NaN        NaN           NaN  ...   
post office           NaN        NaN        NaN        NaN           NaN  ...   
fishing rod           NaN        NaN        NaN        NaN           NaN  ...   
March                 NaN        NaN        NaN        NaN           NaN  ...   
May                   NaN        NaN        NaN        NaN           NaN  ...   

             reproduction_vanarsdall  person_vanarsdall  goals_vanarsdall  \
'em                              NaN                NaN               NaN   
'neath                           NaN                NaN               NaN   
're                              NaN                NaN               NaN   
'shun                            NaN                NaN               NaN   
'tis                             NaN                NaN               NaN   
...                              ...                ...               ...   
shrick                           NaN                NaN               NaN   
post office                      NaN                NaN               NaN   
fishing rod                      NaN                NaN               NaN   
March                            NaN                NaN               NaN   
May                              NaN                NaN               NaN   

             movement_vanarsdall  concreteness_vanarsdall  \
'em                          NaN                      NaN   
'neath                       NaN                      NaN   
're                          NaN                      NaN   
'shun                        NaN                      NaN   
'tis                         NaN                      NaN   
...                          ...                      ...   
shrick                       NaN                      NaN   
post office                  NaN                      NaN   
fishing rod                  NaN                      NaN   
March                        NaN                      NaN   
May                          NaN                      NaN   

             familiarity_vanarsdall  imageability_vanarsdall  \
'em                             NaN                      NaN   
'neath                          NaN                      NaN   
're                             NaN                      NaN   
'shun                           NaN                      NaN   
'tis                            NaN                      NaN   
...                             ...                      ...   
shrick   

In [ ]:
# Log transforming selected norms
with open('../../data/processed/norms_to_log.pkl', 'rb') as f:
    norms_to_log = pickle.load(f)
    norms[norms_to_log] = norms[norms_to_log].apply(np.log1p)

with open('../../data/raw/embed_to_dtype.json', 'r') as f:
    embed_to_type = json.load(f)
embed_to_type

## Cross Validation

In [3]:
# Ridge
alphas = np.logspace(-3, 3, 6)
ridge = RidgeCV(alphas=alphas)

# Logistic hyperparameters
Cs = 1 / alphas
inner_cv = 5
penalty = 'l2'

# Scorers
binary_scorer = make_binary_scorer()
multiclass_scorer = make_multiclass_scorer()

# outer_cv setting 
outer_cv, n_jobs = 5, 8

[1.00000000e-03 1.58489319e-02 2.51188643e-01 3.98107171e+00
 6.30957344e+01 1.00000000e+03]


In [6]:
# RCA
rca = []
for embed_name in tqdm(embeds.keys()):
    embed = embeds[embed_name]
    
    to_print = []
    for norm_name in tqdm(norms.columns, desc=embed_name):
        
        # Aligning data
        y = norms[norm_name].dropna()
        X, y = embed.align(y, axis=0, join='inner', copy=True)
        
        # Checking norm dtype 
        norm_dtype = norm_metadata.loc[norm_name, 'type']
        
        # Solvers, scoring, estimators
        if norm_dtype in ['binary', 'multiclass']:
            X, y = process_categorical(outer_cv, inner_cv, X, y)
            
            # may have switched form multi to bin after processing
            norm_dtype = 'binary' if len(y.unique()) == 2 else 'multiclass'
            
            # Cross validation settings for logistic regression
            solver = best_logistic_solver(X, norm_dtype)
            
            # Defining logistic regression 
            estimator = LogisticRegressionCV(
                Cs=Cs, penalty=penalty, cv=StratifiedKFold(inner_cv),
                solver=solver, n_jobs=8
            )
            scoring = binary_scorer if norm_dtype == 'binary' else multiclass_scorer
        else: # continuous
            estimator, scoring = ridge, 'r2'

            
        # Cross validation
        check = checker(
            embed_name, y, norm_dtype, norm_metadata, outer_cv, norm_name
        )
        if check == 'pass':
             scores = k_fold_cross_val(estimator, X, y, outer_cv, scoring, n_jobs)
             r2_mean, r2_sd = scores.mean(), scores.std()
        else:
            r2_mean, r2_sd = np.nan, np.nan
            
        # Saving
        train_n = int(((outer_cv - 1) / outer_cv) * len(X))
        p = X.shape[1]
        embed_type = embed_to_type[embed_name]
        rca.append([embed_name, embed_type, norm_name, train_n, p, r2_mean, r2_sd, check])
        
        to_print.append([norm_name, train_n, r2_mean, r2_sd, check])

    to_print = pd.DataFrame(to_print, columns=['norm' , 'train_n', 'r2_mean', 'r2_sd', 'check'])
    print(to_print.sort_values('r2_mean', ascending=False).head(10))

rca = pd.DataFrame(rca, columns=['embed', 'embed_type', 'norm', 'train_n', 'p', 'r2_mean', 'r2_sd', 'check'])
rca.to_csv('../../data/final/rca.csv', index=False)
rca

  0%|          | 0/25 [00:00<?, ?it/s]

CBOW_GoogleNews:   0%|          | 0/292 [00:00<?, ?it/s]

/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not conver

                        norm  train_n   r2_mean     r2_sd check
270  meaningfulness_anderson       44  0.920117  0.050454  pass
281       thought_vanarsdall      960  0.805612  0.021746  pass
284         goals_vanarsdall      960  0.802631  0.025427  pass
283        person_vanarsdall      960  0.799361  0.014477  pass
218            valence_britz      380  0.794689  0.035882  pass
219         social_des_britz      380  0.789339  0.037873  pass
162          goals_wilkowski      842  0.787918  0.024260  pass
24              Conc_Glasgow     3694  0.781725  0.009272  pass
177      concreteness_hollis      830  0.778592  0.015293  pass
282  reproduction_vanarsdall      960  0.778579  0.023920  pass


PPMI_SVD_SouthFlorida:   0%|          | 0/292 [00:00<?, ?it/s]

...

                      norm  train_n   r2_mean     r2_sd check
218          valence_britz      399  0.824315  0.103275  pass
219       social_des_britz      399  0.819899  0.090364  pass
283      person_vanarsdall      960  0.815933  0.028905  pass
281     thought_vanarsdall      960  0.809162  0.020676  pass
284       goals_vanarsdall      960  0.805430  0.020911  pass
213  tabooness_janschewitz      368  0.787859  0.041488  pass
162        goals_wilkowski      848  0.756371  0.103501  pass
175         valence_hollis      831  0.747624  0.074644  pass
255   likableness_chandler      767  0.746641  0.084984  pass
280      living_vanarsdall      960  0.741454  0.025185  pass


THINGS:   0%|          | 0/292 [00:00<?, ?it/s]

/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not conver

                        norm  train_n   r2_mean     r2_sd check
105         Biomotion_Binder      128  0.867574  0.038378  pass
280        living_vanarsdall      376  0.843066  0.018136  pass
282  reproduction_vanarsdall      376  0.828345  0.025951  pass
35            Gustatory_Lanc     1235  0.813892  0.040897  pass
111              Body_Binder      128  0.797362  0.067834  pass
124             Taste_Binder      128  0.793488  0.107142  pass
122             Music_Binder      128  0.758826  0.076604  pass
104            Motion_Binder      128  0.726740  0.025597  pass
131              Path_Binder      128  0.725024  0.064865  pass
281       thought_vanarsdall      376  0.724527  0.083121  pass


embed embed_type                     norm  train_n    p  \
0     CBOW_GoogleNews       text                 Freq_HAL    51174  300   
1     CBOW_GoogleNews       text                  Freq_KF    26605  300   
2     CBOW_GoogleNews       text           Freq_SUBTLEXUS    43939  300   
3     CBOW_GoogleNews       text           Freq_SUBTLEXUK    47398  300   
4     CBOW_GoogleNews       text                Freq_Blog    53251  300   
...               ...        ...                      ...      ...  ...   
7295           THINGS   behavior   familiarity_vanarsdall      376   49   
7296           THINGS   behavior  imageability_vanarsdall      376   49   
7297           THINGS   behavior         familiarity_fear      173   49   
7298           THINGS   behavior                 aoa_fear      173   49   
7299           THINGS   behavior        imageability_fear      173   49   

       r2_mean     r2_sd check  
0     0.422344  0.006255  pass  
1     0.463358  0.009852  pass  
2     0.488748  0.006706  pass  
3     0.479608  0.008173  pass  
4     0.463084  0.006165  pass  
...        ...       ...   ...  
7295  0.060692  0.083942  pass  
7296  0.053593  0.095680  pass  
7297  0.139160  0.160894  pass  
7298 -0.021206  0.121789  pass  
7299 -0.054670  0.126442  pass  

[7300 rows x 8 columns]